
<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning">
</div>



# LAB - Building Multi-stage AI System

In this lab, you will construct a multi-stage reasoning system using Databricks' features and LangChain.

You will start by building the first chain, which performs a search using a dataset containing product descriptions from Etsy. Following that, you will create the second chain, which creates an image for the proposed product. Finally, you will integrate these chains to form a complete multi-stage AI system.


**Lab Outline:**

In this lab, you will need to complete the following tasks;

* **Task 1:** Create a Vector Store

* **Task 2:** Build the First Chain (Vector Store Search)

* **Task 3:** Build the Second Chain (Product Image)

* **Task 4:**  Integrate Chains into a Multi-chain System

**📝 Your task:** Complete the **`<FILL_IN>`** sections in the code blocks and follow the other steps as instructed.

## REQUIRED - SELECT CLASSIC COMPUTE
Before executing cells in this notebook, please select your classic compute cluster in the lab. Be aware that **Serverless** is enabled by default.

Follow these steps to select the classic compute cluster:
1. Navigate to the top-right of this notebook and click the drop-down menu to select your cluster. By default, the notebook will use **Serverless**.

2. If your cluster is available, select it and continue to the next cell. If the cluster is not shown:

   - Click **More** in the drop-down.
   
   - In the **Attach to an existing compute resource** window, use the first drop-down to select your unique cluster.

**NOTE:** If your cluster has terminated, you might need to restart it in order to select it. To do this:

1. Right-click on **Compute** in the left navigation pane and select *Open in new tab*.

2. Find the triangle icon to the right of your compute cluster name and click it.

3. Wait a few minutes for the cluster to start.

4. Once the cluster is running, complete the steps above to select your cluster.

## Requirements

Please review the following requirements before starting the lesson:

* To run this notebook, you need to use one of the following Databricks runtime(s): **15.4.x-cpu-ml-scala2.12**


## Classroom Setup

Before starting the lab, run the provided classroom setup script. This script will define configuration variables necessary for the lab. Execute the following cell:

In [0]:
%pip install -U -qq databricks-sdk databricks-vectorsearch langchain-databricks langchain==0.3.7 langchain-community==0.3.7

dbutils.library.restartPython()

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%run ../Includes/Classroom-Setup-02LAB

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


30
30



The examples and models presented in this course are intended solely for demonstration and educational purposes.
 Please note that the models and prompt examples may sometimes contain offensive, inaccurate, biased, or harmful content.


**Other Conventions:**

Throughout this demo, we'll refer to the object `DA`. This object, provided by Databricks Academy, contains variables such as your username, catalog name, schema name, working directory, and dataset locations. Run the code block below to view these details:

In [0]:
print(f"Username:          {DA.username}")
print(f"Catalog Name:      {DA.catalog_name}")
print(f"Schema Name:       {DA.schema_name}")
print(f"Working Directory: {DA.paths.working_dir}")
print(f"Dataset Location:  {DA.paths.datasets}")

Username:          labuser11182879_1754974636@vocareum.com
Catalog Name:      dbacademy
Schema Name:       labuser11182879_1754974636
Working Directory: /Volumes/dbacademy/ops/labuser11182879_1754974636@vocareum_com
Dataset Location:  NestedNamespace (dais='/Volumes/dbacademy_dais/v01', docs='/Volumes/dbacademy_docs/v01')


## Load Dataset

Before you start building the AI chain, you need to load and prepare the dataset and save it as a Delta table.  
For this demo, we will use the **[Databricks Documentation Dataset](/marketplace/consumer/listings/03bbb5c0-983d-4523-833a-57e994d76b3b?o=1120757972560637)** available from the Databricks Marketplace.

This dataset contains documentation pages with associated `id`, `url`, and `content`.  
We will format the data to create a single unified `document` field combining the URL and content, which will then be used to build a Vector Store.

The table will be created for you in the next code block.

In [0]:
## Load the docs table from Unity Catalog
vs_source_table_fullname = f"{DA.catalog_name}.{DA.schema_name}.docs"
create_docs_table(vs_source_table_fullname)
## Display a sample of the data
display(spark.sql(f"SELECT * FROM {vs_source_table_fullname}"))

Validation of table dbacademy_docs.v01.docs complete. No errors found.


id document 22693 ## URL: https://docs.databricks.com/en/admin/access-control/auth-external.html

## Content: Enable authentication to external Databricks services 
Databricks administrators can enable users to authenticate directly to external Databricks services like the Ideas Portal and the Help Center using their Databricks workspace credentials. 
Requirements
Requirements
This feature requires the Premium plan or above.

Ideas Portal
Ideas Portal
The Ideas Portal, powered by Aha!, lets you provide product feedback, vote up product ideas, and check on the progress of your favorite ideas. When you enable authentication to the Ideas Portal, all of your users will be able to access the Ideas Portal using delegated Databricks authentication: as long as they have an active Databricks workspace session, they will be signed into the Ideas Portal automatically. They can go to the workspace help menu (click the question mark in the upper right) and click Feedback, or they can use the Databricks SSO login option when they go to ideas.databricks.com. If they do not have an active Databricks workspace session, they will be prompted to log into Databricks and then taken to the Ideas Portal. 
For more information about the Ideas Portal, see Submit product feedback. 
Access to the Ideas Portal is enabled by default for all users in your workspace. To change access: 
Go to the settings page. 
Click the Advanced tab. 
Click the Authentication to Ideas Portal toggle. 
Click Confirm.

Help Center
Help Center
If your organization has a Databricks Support contract, your authorized support contacts can use the Help Center, powered by Salesforce, to submit and monitor support cases. Users who are not support contacts can use the Help Center to search for help across multiple Databricks content sites without having to authenticate. 
When you enable authentication to the Help Center, users will be able to access the case submission and monitoring interface in the Help Center using delegated Databricks authentication, as long as their Databricks username for this workspace is registered in Salesforce as an authorized support contact. Delegated Databricks authentication signs such users in to the Help Center automatically if they have an active workspace session in their browser. They can go to the workspace help menu (click the question mark in the upper right) and click Support, or they can use the Databricks Sign-in option when they go to the Help Center. If they do not have an active Databricks workspace session when they attempt to sign in from the Help Center, they will be prompted to log into Databricks and then taken to the Help Center. 
For more information about the support process, see Support. 
Access to the Help Center is enabled by default for all users who meet the criteria described above. To change access: 
Go to the settings page. 
Click the Advanced tab. 
Click the Authentication to Help Center toggle. 
Click Confirm. 22694 ## URL: https://docs.databricks.com/en/admin/access-control/tokens.html

## Content: Monitor and manage personal access tokens 
To authenticate to the Databricks REST API, a user can create a personal access token and use it in their REST API request. This article explains how workspace admins can manage personal access tokens in their workspace. 
To create a personal access token, see Databricks personal access token authentication. 
To create a personal access token on behalf of a service principal, see Manage tokens for a service principal. 
Overview of personal access token management
Overview of personal access token management
Personal access tokens are enabled by default for all Databricks workspaces that were created in 2018 or later. 
When personal access tokens are enabled on a workspace, users with the CAN USE permission can generate personal access tokens to access Databricks REST APIs, and they can generate these tokens with any expiration date they like, including an indefinite lifetime. By defaul

%md 
## Create a Vector Store

In this step, you will compute embeddings for the dataset containing information about the products and store them in a Vector Search index using Databricks Vector Search.

**🚨IMPORTANT: Vector Search endpoints must be created before running the rest of the demo. These are already created for you in Databricks Lab environment.**


In [0]:
## Assign Vector Search endpoint by username
vs_endpoint_prefix = "vs_endpoint_"
vs_endpoint_name = vs_endpoint_prefix + str(get_fixed_integer(DA.unique_name("_")))
print(f"Assigned Vector Search endpoint name: {vs_endpoint_name}.")

Assigned Vector Search endpoint name: vs_endpoint_4.


In [0]:
## Index table name
vs_index_table_fullname = f"{DA.catalog_name}.{DA.schema_name}.doc_embeddings"

## Store embeddings in vector store
## NOTE: we're using 'content' as the embedding column
create_vs_index(vs_endpoint_name, vs_index_table_fullname, vs_source_table_fullname, "document" )

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().
[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().
Endpoint named vs_endpoint_4 is ready.


## Task 1: Build the First Chain (Vector Store Search)

In this task, you will create first chain that will search for product details from the Vector Store using a dataset containing product descriptions.

**Instructions:**
   - Configure components for the first chain to perform a search using the Vector Store.
   - Utilize the loaded dataset to generate prompts for Vector Store search queries.
   - Set up retrieval to extract relevant product details based on the generated prompts and search results.


In [0]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain.prompts import PromptTemplate
from langchain_databricks import ChatDatabricks, DatabricksVectorSearch
from langchain_core.output_parsers import StrOutputParser

## Define the Databricks Chat model: llama-3
llm_llama = ChatDatabricks(endpoint="databricks-meta-llama-3-3-70b-instruct", max_tokens=1000)

## Define the prompt template for generating search queries
prompt_template_vs = PromptTemplate.from_template(
    """
    You are a documentation assistant. Based on the following context from a technical document, generate a concise summary or relevant content snippet for answering the user’s question.

    Write a response that is aligned with the tone and format of technical documentation and helps the user understand or resolve their query.

    Maximum 300 words.

    Use the following document snippet and context as example;

    <context>
    {context}
    </context>

    Question: {input}
    """
)

## Construct the RetrievalQA chain for Vector Store search
def get_retriever(persist_dir=None):
    vsc = VectorSearchClient(disable_notice=True)
    vs_index = vsc.get_index(vs_endpoint_name, vs_index_table_fullname)
    vectorstore = DatabricksVectorSearch(vs_index_table_fullname)
    return vectorstore.as_retriever(search_kwargs={"k": 3})

## Construct the chain for question-answering
question_answer_chain = create_stuff_documents_chain(llm_llama, prompt_template_vs)
chain1 = create_retrieval_chain(get_retriever(), question_answer_chain)

## Invoke the chain with an example query   
response = chain1.invoke({"input": "How do I create a Delta table?"})
print(response['answer'])

/root/.ipykernel/5742/command-3554075450802070-528324449:8: LangChainDeprecationWarning: Use databricks_langchain.ChatDatabricks
  llm_llama = ChatDatabricks(endpoint="databricks-meta-llama-3-3-70b-instruct", max_tokens=1000)
/root/.ipykernel/5742/command-3554075450802070-528324449:33: LangChainDeprecationWarning: Use databricks_langchain.DatabricksVectorSearch
  vectorstore = DatabricksVectorSearch(vs_index_table_fullname)


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().
**Creating a Delta Table**

To create a Delta table, you can use the `CREATE OR REFRESH LIVE TABLE` syntax in SQL. The following example creates a table by loading data from a CSV file stored in a Unity Catalog volume:

```sql
CREATE OR REFRESH LIVE TABLE table_name
COMMENT "Table comment"
AS SELECT * FROM read_files('/path/to/file.csv', format => 'csv', header => true, mode => 'FAILFAST')
```

Replace `table_name` with the desired name for your table, and `/path/to/file.csv` with the path to your CSV file.

**Example Use Case**
--------------------

The following example creates a table named `baby_names_sql_raw` by loading data from a CSV file:
```sql
CREATE OR REFRESH LIVE TABLE baby_names_sql_raw
COMMENT "Popular baby first names in New York. This data

Trace(request_id=tr-eb588853e63b4067b72c034e68cb58d8)

## Task 2: Build the Second Chain (Optimization)

In this step, you will create a second chain to enhance the product details generated by the first chain. This optimization process aims to make the descriptions more compelling and SEO-friendly. In a real-world scenario, this model could be trained on your internal data or fine-tuned to align with your specific business objectives.

**Instructions:**

- Define a second chain using `llama-3-70b-instruct`.  

- Create a prompt to optimize the generated product description. For example:  
  *"You are a marketing expert. Revise the product title and description to be SEO-friendly and more appealing to Databricks users."*

- Use `product_details` as the parameter to be passed into the prompt.  

- Implement the chain and test it with a sample input.  


In [0]:
## Define the Databricks Chat model using llama-3-3-70b-instruct
llm_llama3 = ChatDatabricks(endpoint="databricks-meta-llama-3-3-70b-instruct", max_tokens=1000)

## Define the prompt template for refining documentation output
doc_optimization_prompt = PromptTemplate.from_template(
    """
    You are a technical writer. Improve the following documentation snippet to make it clearer, concise, and aligned with the tone used in Databricks documentation.

    Documentation snippet: {doc_snippet}

    Return only the revised documentation content.
    """
)

## Define chain 2
chain2 = doc_optimization_prompt | llm_llama3 | StrOutputParser()

## Test the chain
chain2.invoke({"doc_snippet": "Query testing product with mobile app control"})

"# Query Testing with Mobile App Control\n=====================================\n\n## Overview\nQuery testing is a crucial step in ensuring the reliability and performance of your data queries. This feature allows you to test and validate your queries directly from your mobile app, providing a seamless and efficient way to verify query results on-the-go.\n\n## Key Features\n- **Remote Query Testing**: Execute and test queries from your mobile device, enabling real-time validation of query performance and results.\n- **App-Controlled Query Management**: Easily manage and monitor your queries, including starting, stopping, and viewing query execution plans, all from the convenience of your mobile app.\n\n## Getting Started\n1. **Install the Mobile App**: Download and install the Databricks mobile app from your device's app store.\n2. **Configure App Settings**: Log in to your Databricks account through the app and configure your settings to enable query testing.\n3. **Execute a Query**: 

Trace(request_id=tr-e4e025a05f5748cca9c04cfd1b2ca3dc)

## Task 3: Integrate Chains into a Multi-chain System

In this task, you will link the individual chains created in Task 2 and Task 3 together to form a multi-chain system that can handle multi-stage reasoning.

**Instructions:**

- Use Databricks **`Llama Chat model`** for processing text inputs, which is defined above in the first task.

- Create a prompt template to generate an **`HTML page`** for displaying generated product details.

- Construct the **`Multi-Chain System`**  by combining the outputs of the previous chains. **Important**: You will need to rename the output of the first chain and second chain while passing them to the next stage. This sequential chain should be as; **chain3 = chain1 > (`product_details`) > chain2 > `(optimized_product_details)` > prompt3**.  

- Invoke the multi-chain system with the input data to generate the HTML page for the specified product.


In [0]:
from langchain.schema.runnable import RunnablePassthrough, RunnableMap
from langchain_core.output_parsers import StrOutputParser
from IPython.display import display, HTML

## Define the prompt template for generating the HTML page
prompt_template_3 = PromptTemplate.from_template(
    """Create an HTML section for the following technical documentation snippet:
    
    Content: {optimized_doc}

    Return valid HTML (no head/body tags).
    """
)

## Construct multi-stage chain
chain3 = (
    chain1
    | RunnableMap({"doc_snippet": lambda x: x["answer"]})
    | chain2
    | RunnableMap({"optimized_doc": lambda x: x})
    | prompt_template_3
    | llm_llama
    | StrOutputParser()
)

## Sample query
query = {
    "input": "How do I create a Delta table in Databricks?"
}

output_html = chain3.invoke(query)

## Display the generated HTML output
display(HTML(output_html))

Trace(request_id=tr-f60aa57f8fa042029cec96da3edad2a8)

## Task 4: Save the Chain to Model Registry in UC

In this task, you will save the multi-stage chain system within our Unity Catalog.

**Instructions:**

- Set the model registry to UC and use the model name defined.

- Log and register the final multi-chain system.

- To test the registered model, load the model back from model registry and query it using a sample query. 

After registering the chain, you can view the chain and models in the **Catalog Explorer**.

In [0]:
from mlflow.models import infer_signature
import mlflow

## Set model registry to UC
mlflow.set_registry_uri("databricks-uc")
model_name = f"{DA.catalog_name}.{DA.schema_name}.multi_stage_doc_chain"

## Log the model
with mlflow.start_run(run_name="multi_stage_doc_chain") as run:
    signature = infer_signature(query, output_html)
    model_info = mlflow.langchain.log_model(
        chain3,
        loader_fn=get_retriever, 
        artifact_path="chain",
        registered_model_name=model_name,
        input_example=query,
        signature=signature
    )

## Load and test the model
model_uri = f"models:/{model_name}/{model_info.registered_model_version}"
model = mlflow.langchain.load_model(model_uri)

output_html = model.invoke(query)
display(HTML(output_html))

/local_disk0/.ephemeral_nfs/envs/pythonEnv-3a4a89af-197f-4d12-a8a6-55794e2f522b/lib/python3.11/site-packages/mlflow/langchain/runnables.py:292: UserWarning: Your model contains a class imported from the LangChain partner package `langchain-databricks`. When loading the model back, MLflow will use the community version of the classes instead of the partner packages, which may lead to unexpected behavior. To ensure that the model is loaded correctly, it is recommended to save the model with the 'model-from-code' method instead: https://mlflow.org/docs/latest/models.html#models-from-code
  warnings.warn(
/local_disk0/.ephemeral_nfs/envs/pythonEnv-3a4a89af-197f-4d12-a8a6-55794e2f522b/lib/python3.11/site-packages/mlflow/langchain/runnables.py:292: UserWarning: Your model contains a class imported from the LangChain partner package `langchain-databricks`. When loading the model back, MLflow will use the community version of the classes instead of the partner packages, which may lead to unexp

[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().


Uploading artifacts:   0%|          | 0/46 [00:00<?, ?it/s]

Successfully registered model 'dbacademy.labuser11182879_1754974636.multi_stage_doc_chain'.


Uploading artifacts:   0%|          | 0/46 [00:00<?, ?it/s]

Created version '1' of model 'dbacademy.labuser11182879_1754974636.multi_stage_doc_chain'.


[NOTICE] Using a notebook authentication token. Recommended for development only. For improved performance, please use Service Principal based authentication. To disable this message, pass disable_notice=True to VectorSearchClient().


Trace(request_id=tr-a79009cb4fac4f11896a0b9500e404ca)


## Conclusion

In this lab, you've learned how to build a multi-stage AI system using Databricks and LangChain. By integrating multiple chains, you can perform complex reasoning tasks such as searching for product details and optimizing the response based on your business needs. This approach enables the development of sophisticated AI systems capable of handling diverse tasks efficiently.



&copy; 2025 Databricks, Inc. All rights reserved. Apache, Apache Spark, Spark, the Spark Logo, Apache Iceberg, Iceberg, and the Apache Iceberg logo are trademarks of the <a href="https://www.apache.org/" target="blank">Apache Software Foundation</a>.<br/>
<br/><a href="https://databricks.com/privacy-policy" target="blank">Privacy Policy</a> | 
<a href="https://databricks.com/terms-of-use" target="blank">Terms of Use</a> | 
<a href="https://help.databricks.com/" target="blank">Support</a>